# Coursera Capstone Project

## The Battle of Neighborhoods - Final Report

### Preston Beamer

# Introduction

### 1.1 Background

Yoga has become a way of life. Millions of people throughout the world are practicing yoga more frequently and the number is expected to increase dramatically over the coming years. Not only are studies supporting this, but you are likely to see the proof yourself throughout your community. People are always seeking a way to beat stress and yoga is one way to do that. It is a relatively low-cost, easy and an enjoyable way to obtain good mental health by boosting your brain chemicals responsible for fighting stress.  

### 1.2 Problem 

The primary idea of this study is to help some partners who are wanting to start a chain of yoga studios in New York. New York City encompasses five boroughs: The Bronx, Brooklyn, Manhattan, Queens, and Staten Island. However, the partners are only interested in three of the five boroughs right now, Manhattan, Brooklyn, and Queens. 
For their first location to become a huge success, they need to do their due-diligence and select the perfect location for their studio. To do this, they need to download the data from: https://geo.nyu.edu/catalog/nyu_2451_34572, covert the addresses into their equivalent latitude and longitude values. Afterwards, they will use the Foursquare API to explore all the neighborhoods in New York City. Once Foursquare has been activated, we will use the explore function to get the most common venue categories in each neighborhood and then group the neighborhoods into clusters. Subsequently, we will then use the k-means algorithm and Folium library to help visualize the three Boroughs and their neighborhoods along with their emerging clusters. Lastly, we will compare this information against the borough’s demographics (Age, Race, Gender, & Income) from the Census Reporter to get a broader picture and narrow down the perfect location for their first studio. 


# Data 

## Upload Libraries Required

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1f             |       h516909a_0         2.1 MB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    certifi-2019.11.28         |   py36h9f0ad1d_1         149 KB  conda-forge
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1

# Downloading Dataset

New York has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood.

You can get the data: https://geo.nyu.edu/catalog/nyu_2451_34572

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [5]:
neighborhoods_data = newyork_data['features']

In [6]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [8]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [9]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [10]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [11]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [12]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


# Mapping New York with neighborhoods superimposed on top

In [13]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [14]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head(40)

Borough         Neighborhood   Latitude  Longitude
0   Manhattan          Marble Hill  40.876551 -73.910660
1   Manhattan            Chinatown  40.715618 -73.994279
2   Manhattan   Washington Heights  40.851903 -73.936900
3   Manhattan               Inwood  40.867684 -73.921210
4   Manhattan     Hamilton Heights  40.823604 -73.949688
5   Manhattan       Manhattanville  40.816934 -73.957385
6   Manhattan       Central Harlem  40.815976 -73.943211
7   Manhattan          East Harlem  40.792249 -73.944182
8   Manhattan      Upper East Side  40.775639 -73.960508
9   Manhattan            Yorkville  40.775930 -73.947118
10  Manhattan           Lenox Hill  40.768113 -73.958860
11  Manhattan     Roosevelt Island  40.762160 -73.949168
12  Manhattan      Upper West Side  40.787658 -73.977059
13  Manhattan       Lincoln Square  40.773529 -73.985338
14  Manhattan              Clinton  40.759101 -73.996119
15  Manhattan              Midtown  40.754691 -73.981669
16  Manhattan          Murray Hill  40.748303 -73.978332
17  Manhattan              Chelsea  40.744035 -74.003116
18  Manhattan    Greenwich Village  40.726933 -73.999914
19  Manhattan         East Village  40.727847 -73.982226
20  Manhattan      Lower East Side  40.717807 -73.980890
21  Manhattan              Tribeca  40.721522 -74.010683
22  Manhattan         Little Italy  40.719324 -73.997305
23  Manhattan                 Soho  40.722184 -74.000657
24  Manhattan         West Village  40.734434 -74.006180
25  Manhattan     Manhattan Valley  40.797307 -73.964286
26  Manhattan  Morningside Heights  40.808000 -73.963896
27  Manhattan             Gramercy  40.737210 -73.981376
28  Manhattan    Battery Park City  40.711932 -74.016869
29  Manhattan   Financial District  40.707107 -74.010665
30  Manhattan        Carnegie Hill  40.782683 -73.953256
31  Manhattan                 Noho  40.723259 -73.988434
32  Manhattan         Civic Center  40.715229 -74.005415
33  Manhattan        Midtown South  40.748510 -73.988713
34  Manhattan         Sutton Place  40.760280 -73.963556
35  Manhattan           Turtle Bay  40.752042 -73.967708
36  Manhattan           Tudor City  40.746917 -73.971219
37  Manhattan      Stuyvesant Town  40.731000 -73.974052
38  Manhattan             Flatiron  40.739673 -73.990947
39  Manhattan         Hudson Yards  40.756658 -74.000111

In [15]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


In [16]:
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

# Foursquare API

In [17]:
CLIENT_ID = 'PYU4MQL3USKXUBOOPTBKKD4AKWSLMGRQVUIRDQGEE1HHDNRQ'
CLIENT_SECRET = '1MLLXLJPVRZOHZTPHR4RMUH3SOIFCKMBQRPB4FVQABJQUJOD'
VERSION = '20202802'
LIMIT = 100
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: PYU4MQL3USKXUBOOPTBKKD4AKWSLMGRQVUIRDQGEE1HHDNRQ
CLIENT_SECRET:1MLLXLJPVRZOHZTPHR4RMUH3SOIFCKMBQRPB4FVQABJQUJOD


In [18]:
manhattan_data.loc[0, 'Neighborhood']

'Marble Hill'

In [19]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = manhattan_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Marble Hill are 40.87655077879964, -73.91065965862981.


In [20]:
radius=500
LIMIT=100

In [21]:

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

In [22]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e85efb8542890001b6810d3'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 24,
  'suggestedBounds': {'ne': {'lat': 40.88105078329964,
    'lng': -73.90471933917806},
   'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b4429abf964a52037f225e3',
       'name': "Arturo's",
       'location': {'address': '5198 Broadway',
        'crossStreet': 'at 225th St.',
        'lat': 40.87441177110231,
        'lng': -73.91027100981574,
        'labeledLatLngs': [{'label'

In [23]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [24]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name   categories        lat        lng
0       Arturo's  Pizza Place  40.874412 -73.910271
1    Bikram Yoga  Yoga Studio  40.876844 -73.906204
2  Tibbett Diner        Diner  40.880404 -73.908937
3        Dunkin'   Donut Shop  40.877136 -73.906666
4      Starbucks  Coffee Shop  40.877531 -73.905582

In [25]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

24 venues were returned by Foursquare.


In [26]:
nearby_venues.head(24)

name           categories        lat  \
0                           Arturo's          Pizza Place  40.874412   
1                        Bikram Yoga          Yoga Studio  40.876844   
2                      Tibbett Diner                Diner  40.880404   
3                            Dunkin'           Donut Shop  40.877136   
4                          Starbucks          Coffee Shop  40.877531   
5   Astral Fitness & Wellness Center                  Gym  40.876705   
6                      Blink Fitness                  Gym  40.877271   
7                          T.J. Maxx     Department Store  40.877232   
8              Land & Sea Restaurant   Seafood Restaurant  40.877885   
9          TCR The Club of Riverdale       Tennis Stadium  40.878628   
10                          Rite Aid             Pharmacy  40.875467   
11                         Starbucks          Coffee Shop  40.873755   
12                Lot Less Closeouts       Discount Store  40.878270   
13                    Vitamin Shoppe      Supplement Shop  40.877160   
14                    Baskin-Robbins       Ice Cream Shop  40.877149   
15                 Subway Sandwiches       Sandwich Place  40.874667   
16                        Five Below   Miscellaneous Shop  40.877256   
17                     Boston Market  American Restaurant  40.877430   
18                            SUBWAY       Sandwich Place  40.878465   
19                   Parrilla Latina           Steakhouse  40.877473   
20              The Children's Place           Kids Store  40.873672   
21                    Broadway Plaza        Shopping Mall  40.877539   
22                            Subway       Sandwich Place  40.877720   
23         Terrace View Delicatessen        Deli / Bodega  40.875995   

          lng  
0  -73.910271  
1  -73.906204  
2  -73.908937  
3  -73.906666  
4  -73.905582  
5  -73.906372  
6  -73.905595  
7  -73.905042  
8  -73.905873  
9  -73.914568  
10 -73.908906  
11 -73.908613  
12 -73.905265  
13 -73.905632  
14 -73.906658  
15 -73.909586  
16 -73.904938  
17 -73.905412  
18 -73.905518  
19 -73.906073  
20 -73.908156  
21 -73.905396  
22 -73.905380  
23 -73.913151

# Exploring the Neighborhoods in Manhatten

In [27]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [28]:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [29]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3293, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066        Dunkin'   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877136       -73.906666     Donut Shop  
4       40.877531       -73.905582    Coffee Shop

In [30]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       86                      86     86   
Carnegie Hill                          100                     100    100   
Central Harlem                          44                      44     44   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                             40                      40     40   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                                98                      98     98   
Greenwich Village                      100                     100    100   
Hamilton Heights                        60                      60     60   
Hudson Yards                            82                      82     82   
Inwood                                  56                      56     56   
Lenox Hill                             100                     100    100   
Lincoln Square                         100                     100    100   
Little Italy                           100                     100    100   
Lower East Side                         58                      58     58   
Manhattan Valley                        51                      51     51   
Manhattanville                          43                      43     43   
Marble Hill                             24                      24     24   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     40                      40     40   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        28                      28     28   
Soho                                   100                     100    100   
Stuyvesant Town                         18                      18     18   
Sutton Place                           100                     100    100   
Tribeca                                 97                      97     97   
Tudor City                              79                      79     79   
Turtle Bay                             100                     100    100   
Upper East Side                        100                     100    100   
Upper West Side                        100                     100    100   
Washington Heights                      89                      89     89   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                86               86              86  
Carnegie Hill                   100              100             100  
Central Harlem                   44               44              44  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                      40               40              40  
East Village                    100              100             100  
Finan

In [31]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 333 uniques categories.


# Analyzing Each Neighborhood

In [32]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Acupuncturist  Adult Boutique  \
0  Marble Hill                  0              0               0   
1  Marble Hill                  0              0               0   
2  Marble Hill                  0              0               0   
3  Marble Hill                  0              0               0   
4  Marble Hill                  0              0               0   

   Afghan Restaurant  African Restaurant  American Restaurant  Antique Shop  \
0                  0                   0                    0             0   
1                  0                   0                    0             0   
2                  0                   0                    0             0   
3                  0                   0                    0             0   
4                  0                   0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  BBQ Joint  Baby Store  \
0                      0                    0          0           0   
1                      0                    0          0           0   
2                      0                    0          0           0   
3                      0                    0          0           0   
4                      0                    0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0                0         0            0           0   
1                0         0            0           0   
2                0         0            0           0   
3                0         0            0           0   
4                0         0            0           0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   Breakfast Spot  Bridal Shop  Bridge  Bubble Tea Shop  Building  \
0               0 

In [33]:
manhattan_onehot.shape

(3293, 334)

## Group rows by neighborhood and by taking the mean of the fequency of occurrence of each category

In [34]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Acupuncturist  Adult Boutique  \
0     Battery Park City           0.000000           0.00            0.00   
1         Carnegie Hill           0.000000           0.00            0.00   
2        Central Harlem           0.000000           0.00            0.00   
3               Chelsea           0.000000           0.00            0.00   
4             Chinatown           0.000000           0.00            0.00   
5          Civic Center           0.000000           0.00            0.00   
6               Clinton           0.000000           0.00            0.00   
7           East Harlem           0.000000           0.00            0.00   
8          East Village           0.000000           0.00            0.00   
9    Financial District           0.010000           0.00            0.00   
10             Flatiron           0.000000           0.01            0.00   
11             Gramercy           0.000000           0.00            0.00   
12    Greenwich Village           0.000000           0.00            0.00   
13     Hamilton Heights           0.000000           0.00            0.00   
14         Hudson Yards           0.000000           0.00            0.00   
15               Inwood           0.000000           0.00            0.00   
16           Lenox Hill           0.000000           0.00            0.00   
17       Lincoln Square           0.000000           0.00            0.00   
18         Little Italy           0.000000           0.00            0.00   
19      Lower East Side           0.000000           0.00            0.00   
20     Manhattan Valley           0.000000           0.00            0.00   
21       Manhattanville           0.000000           0.00            0.00   
22          Marble Hill           0.000000           0.00            0.00   
23              Midtown           0.000000           0.00            0.00   
24        Midtown South           0.000000           0.00            0.00   
25  Morningside Heights           0.000000           0.00            0.00   
26          Murray Hill           0.000000           0.00            0.00   
27                 Noho           0.000000           0.00            0.00   
28     Roosevelt Island           0.000000           0.00            0.00   
29                 Soho           0.010000           0.00            0.00   
30      Stuyvesant Town           0.000000           0.00            0.00   
31         Sutton Place           0.000000           0.00            0.01   
32              Tribeca           0.000000           0.00            0.00   
33           Tudor City           0.000000           0.00            0.00   
34           Turtle Bay           0.000000           0.00            0.00   
35      Upper East Side           0.000000           0.00            0.00   
36      Upper West Side           0.010000           0.00            0.00   
37   Washington Heights           0.011236           0.00            0.00   
38         West Village           0.000000           0.00            0.00   
39            Yorkville           0.000000           0.00            0.00   

    Afghan Restaurant  African Restaurant  American Restaurant  Antique Shop  \
0                0.00            0.000000             0.011628          0.00   
1                0.00            0.000000             0.010000          0.00   
2                0.00            0.068182             0.045455          0.00   
3                0.00            0.000000             0.030000          0.00   
4                0.00            0.000000             0.040000          0.00   
5                0.00            0.000000             0.030000          0.01   
6                0.00            0.000000             0.040000          0.00   
7                0.00            0.000000             0.000000          0.00   
8                0.00            0.000000             0.020000          0.00   
9                0.00            0.000000            

## Top 5 Most Common Venues In Each Venue

In [35]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
           venue  freq
0           Park  0.07
1          Hotel  0.06
2    Coffee Shop  0.06
3  Boat or Ferry  0.03
4      Wine Shop  0.03


----Carnegie Hill----
                  venue  freq
0           Coffee Shop  0.06
1           Pizza Place  0.06
2                  Café  0.05
3  Gym / Fitness Center  0.03
4        Cosmetics Shop  0.03


----Central Harlem----
                 venue  freq
0   African Restaurant  0.07
1        Deli / Bodega  0.05
2  American Restaurant  0.05
3                  Bar  0.05
4   Seafood Restaurant  0.05


----Chelsea----
                venue  freq
0         Coffee Shop  0.07
1              Bakery  0.06
2  Italian Restaurant  0.04
3      Ice Cream Shop  0.03
4               Hotel  0.03


----Chinatown----
                 venue  freq
0   Chinese Restaurant  0.09
1         Cocktail Bar  0.05
2  American Restaurant  0.04
3                  Spa  0.03
4         Optical Shop  0.03


----Civic Center----
                  venue  freq


In [36]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [37]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park                 Hotel   
1      Carnegie Hill           Pizza Place           Coffee Shop   
2     Central Harlem    African Restaurant         Deli / Bodega   
3            Chelsea           Coffee Shop                Bakery   
4          Chinatown    Chinese Restaurant          Cocktail Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop                   Gym             Wine Shop   
1                  Café                Bakery  Gym / Fitness Center   
2   American Restaurant                   Bar     French Restaurant   
3    Italian Restaurant                 Hotel   American Restaurant   
4   American Restaurant          Optical Shop                Bakery   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0         Boat or Ferry          Memorial Site           Pizza Place   
1                   Gym    Japanese Restaurant     French Restaurant   
2    Seafood Restaurant     Chinese Restaurant             Cafeteria   
3        Ice Cream Shop              Nightclub             Bookstore   
4          Dessert Shop  Vietnamese Restaurant    Salon / Barbershop   

  9th Most Common Venue 10th Most Common Venue  
0    Italian Restaurant              BBQ Joint  
1        Cosmetics Shop              Bookstore  
2              Boutique               Beer Bar  
3                Market      French Restaurant  
4                   Spa      Hotpot Restaurant

# Cluster Neighborhoods

In [38]:
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 1, 0, 1, 4, 0, 0, 4, 1, 0], dtype=int32)

In [39]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head()

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               3   
1  Manhattan           Chinatown  40.715618 -73.994279               4   
2  Manhattan  Washington Heights  40.851903 -73.936900               4   
3  Manhattan              Inwood  40.867684 -73.921210               4   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place                   Gym           Coffee Shop   
1    Chinese Restaurant          Cocktail Bar   American Restaurant   
2                  Café         Grocery Store                Bakery   
3                  Café    Mexican Restaurant           Pizza Place   
4           Pizza Place                  Café           Coffee Shop   

  4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
0           Yoga Studio              Pharmacy                 Steakhouse   
1          Optical Shop                Bakery               Dessert Shop   
2    Chinese Restaurant     Mobile Phone Shop  Latin American Restaurant   
3                Lounge            Restaurant         Chinese Restaurant   
4         Deli / Bodega    Mexican Restaurant                Yoga Studio   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0          Shopping Mall    Seafood Restaurant           Pizza Place   
1  Vietnamese Restaurant    Salon / Barbershop                   Spa   
2                   Bank        Sandwich Place      Tapas Restaurant   
3     Frozen Yogurt Shop   American Restaurant                  Park   
4         Sandwich Place      Sushi Restaurant                Bakery   

  10th Most Common Venue  
0          Deli / Bodega  
1      Hotpot Restaurant  
2            Coffee Shop  
3                 Bakery  
4   Caribbean Restaurant

In [40]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examine 5 Clusters

We have to examine each cluster in order to determine the disciminating venue categories that make up each cluster.

### Cluster 1

In [41]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
6        Central Harlem    African Restaurant            Deli / Bodega   
9             Yorkville    Italian Restaurant                      Gym   
11     Roosevelt Island        Sandwich Place                     Park   
13       Lincoln Square    Italian Restaurant                    Plaza   
14              Clinton               Theater       Italian Restaurant   
21              Tribeca   American Restaurant                     Park   
24         West Village    Italian Restaurant  New American Restaurant   
26  Morningside Heights                  Park      American Restaurant   
27             Gramercy                   Bar       Italian Restaurant   
28    Battery Park City                  Park                    Hotel   
29   Financial District           Coffee Shop      American Restaurant   
32         Civic Center           Coffee Shop     Gym / Fitness Center   
35           Turtle Bay           Coffee Shop       Italian Restaurant   
39         Hudson Yards   American Restaurant       Italian Restaurant   

   3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
6    American Restaurant                   Bar      French Restaurant   
9            Coffee Shop                   Bar          Deli / Bodega   
11           Coffee Shop                School           Liquor Store   
13               Theater                  Café  Performing Arts Venue   
14  Gym / Fitness Center   American Restaurant                    Spa   
21    Italian Restaurant                   Spa                   Café   
24   American Restaurant              Wine Bar                   Park   
26           Coffee Shop             Bookstore         Sandwich Place   
27   American Restaurant           Pizza Place             Bagel Shop   
28           Coffee Shop                   Gym              Wine Shop   
29                   Bar           Pizza Place                    Gym   
32     French Restaurant                 Hotel            Yoga Studio   
35            Steakhouse              Wine Bar       Sushi Restaurant   
39                 Hotel  Gym / Fitness Center                   Café   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6     Seafood Restaurant    Chinese Restaurant             Cafeteria   
9            Pizza Place    Mexican Restaurant   Japanese Restaurant   
11           Supermarket         Metro Station              Bus Line   
13   American Restaurant          Concert Hall   Indie Movie Theater   
14           Coffee Shop        Sandwich Place             Wine Shop   
21              Wine Bar           Coffee Shop      Greek Restaurant   
24             Jazz Club          Cocktail Bar           Coffee Shop   
26         Deli / Bodega          Burger Joint    Seafood Restaurant   
27    Mexican Restaurant                 Hotel          Cocktail Bar   
28         Boat or Ferry         Memorial Site           Pizza Place   
29            Food Truck            Steakhouse          Cocktail Bar   
32   American Restaurant                   Spa        Sandwich Place   
35                  Park                 Hotel                  Café   
39           Coffee Shop       Thai Restaurant      Asian Restaurant   

   9th Most Common Venue    10th Most Common Venue  
6               Boutique                  Beer Bar  
9                  Diner          Sushi Restaurant  
11        Farmers Market              Soccer Field  
13  Gym / Fitness Center                 Wine Shop  
14                   Gym                     Hotel  
21           Men's Store         French Restaurant  
24               Theater                    Bakery  
26           Supermarket  Mediterranean Restaurant  
27            Playground            Ice Cream Shop  
28    Italian Restaurant                 BBQ Joint  
29  Gym / Fitness Center       Japanese Restaurant  
32                  Park              Cocktail Bar  
35     Indian Restaurant          

### Cluster 2

In [42]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8     Upper East Side    Italian Restaurant           Coffee Shop   
10         Lenox Hill    Italian Restaurant           Coffee Shop   
12    Upper West Side    Italian Restaurant                   Bar   
15            Midtown                 Hotel            Steakhouse   
16        Murray Hill           Coffee Shop        Sandwich Place   
17            Chelsea           Coffee Shop                Bakery   
18  Greenwich Village    Italian Restaurant        Clothing Store   
19       East Village                   Bar        Ice Cream Shop   
22       Little Italy                Bakery                  Café   
23               Soho        Clothing Store         Women's Store   
30      Carnegie Hill           Pizza Place           Coffee Shop   
31               Noho    Italian Restaurant     French Restaurant   
33      Midtown South     Korean Restaurant   Japanese Restaurant   
34       Sutton Place  Gym / Fitness Center    Italian Restaurant   
38           Flatiron           Yoga Studio  Gym / Fitness Center   

   3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
8                 Bakery               Exhibit                 Juice Bar   
10      Sushi Restaurant           Pizza Place              Cocktail Bar   
12           Coffee Shop              Wine Bar  Mediterranean Restaurant   
15           Coffee Shop        Clothing Store                 Bookstore   
16   American Restaurant   Japanese Restaurant                     Hotel   
17    Italian Restaurant                 Hotel       American Restaurant   
18      Sushi Restaurant                  Café         Indian Restaurant   
19    Mexican Restaurant              Wine Bar               Pizza Place   
22       Bubble Tea Shop                 Hotel        Italian Restaurant   
23    Italian Restaurant              Boutique                    Bakery   
30                  Café                Bakery      Gym / Fitness Center   
31                 Hotel          Cocktail Bar               Coffee Shop   
33          Dessert Shop                 Hotel                 Hotel Bar   
34           Coffee Shop                   Gym       American Restaurant   
38                   Spa   Japanese Restaurant                      Café   

       6th Most Common Venue     7th Most Common Venue  \
8       Gym / Fitness Center               Art Gallery   
10              Burger Joint                      Café   
12         Indian Restaurant                    Bakery   
15                    Bakery         French Restaurant   
16      Gym / Fitness Center        Italian Restaurant   
17            Ice Cream Shop                 Nightclub   
18         French Restaurant           Bubble Tea Shop   
19              Cocktail Bar        Chinese Restaurant   
22            Sandwich Place  Mediterranean Restaurant   
23  Mediterranean Restaurant                Shoe Store   
30                       Gym       Japanese Restaurant   
31               Pizza Place               Art Gallery   
33               Salad Place       American Restaurant   
34         Indian Restaurant    Furniture / Home Store   
38       American Restaurant              Cycle Studio   

       8th Most Common Venue     9th Most Common Venue  \
8          French Restaurant               Yoga Studio   
10                       Gym      Gym / Fitness Center   
12                      Café            Ice Cream Shop   
15                      Café                   Theater   
16  Mediterranean Restaurant              Cocktail Bar   
17                 Bookstore                    Market   
18        Seafood Restaurant            Cosmetics Shop   
19        Italian Restaurant         Korean Restaurant   
22              Cocktail Bar        Salon / Barbershop   
23                     Hotel       Sporting Goods Shop   
30         French Restaurant            Cosmetics Shop   
31       American Restaurant                 Gift Shop   
33  

### Cluster 3

In [43]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37  Stuyvesant Town                   Bar                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
37           Gas Station  Gym / Fitness Center        Baseball Field   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
37     German Restaurant       Harbor / Marina          Cocktail Bar   

   9th Most Common Venue 10th Most Common Venue  
37           Coffee Shop                 Bistro

### Cluster 4

In [44]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Marble Hill        Sandwich Place                   Gym   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop           Yoga Studio              Pharmacy   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Steakhouse         Shopping Mall    Seafood Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0           Pizza Place          Deli / Bodega

### Cluster 5 

In [45]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
1            Chinatown    Chinese Restaurant          Cocktail Bar   
2   Washington Heights                  Café         Grocery Store   
3               Inwood                  Café    Mexican Restaurant   
4     Hamilton Heights           Pizza Place                  Café   
5       Manhattanville           Coffee Shop    Seafood Restaurant   
7          East Harlem    Mexican Restaurant                Bakery   
20     Lower East Side    Chinese Restaurant                  Café   
25    Manhattan Valley           Pizza Place     Indian Restaurant   
36          Tudor City    Mexican Restaurant                  Café   

   3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
1    American Restaurant          Optical Shop                     Bakery   
2                 Bakery    Chinese Restaurant          Mobile Phone Shop   
3            Pizza Place                Lounge                 Restaurant   
4            Coffee Shop         Deli / Bodega         Mexican Restaurant   
5     Italian Restaurant                  Park         Mexican Restaurant   
7        Thai Restaurant           Pizza Place  Latin American Restaurant   
20           Art Gallery           Pizza Place                Coffee Shop   
25                   Bar           Coffee Shop         Mexican Restaurant   
36                  Park         Deli / Bodega           Greek Restaurant   

        6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
1                Dessert Shop  Vietnamese Restaurant    Salon / Barbershop   
2   Latin American Restaurant                   Bank        Sandwich Place   
3          Chinese Restaurant     Frozen Yogurt Shop   American Restaurant   
4                 Yoga Studio         Sandwich Place      Sushi Restaurant   
5         Dumpling Restaurant      Food & Drink Shop            Bike Trail   
7               Deli / Bodega             Taco Place          Cocktail Bar   
20               Cocktail Bar    Japanese Restaurant      Ramen Restaurant   
25                 Playground        Thai Restaurant    Chinese Restaurant   
36                Coffee Shop            Pizza Place      Asian Restaurant   

   9th Most Common Venue 10th Most Common Venue  
1                    Spa      Hotpot Restaurant  
2       Tapas Restaurant            Coffee Shop  
3                   Park                 Bakery  
4                 Bakery   Caribbean Restaurant  
5                 Lounge       Sushi Restaurant  
7               Pharmacy               Beer Bar  
20        Sandwich Place                 Bakery  
25     French Restaurant   Gym / Fitness Center  
36       Thai Restaurant     Spanish Restaurant

In [46]:
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
brooklyn_data.head()

Borough Neighborhood   Latitude  Longitude
0  Brooklyn    Bay Ridge  40.625801 -74.030621
1  Brooklyn  Bensonhurst  40.611009 -73.995180
2  Brooklyn  Sunset Park  40.645103 -74.010316
3  Brooklyn   Greenpoint  40.730201 -73.954241
4  Brooklyn    Gravesend  40.595260 -73.973471

# Brookyln Data

In [47]:
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Brooklyn are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Brooklyn are 40.6501038, -73.9495823.


In [48]:
map_brooklyn = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(brooklyn_data['Latitude'], brooklyn_data['Longitude'], brooklyn_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_brooklyn)  
    
map_brooklyn

In [49]:
brooklyn_data.loc[0, 'Neighborhood']

'Bay Ridge'

In [50]:
neighborhood_latitude = brooklyn_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = brooklyn_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = brooklyn_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Bay Ridge are 40.625801065010656, -74.03062069353813.


In [51]:
radius=500
LIMIT=100

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

In [52]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e85f12fdf2774001ce93aaa'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Bay Ridge',
  'headerFullLocation': 'Bay Ridge, Brooklyn',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 85,
  'suggestedBounds': {'ne': {'lat': 40.63030106951066,
    'lng': -74.02470273356597},
   'sw': {'lat': 40.62130106051065, 'lng': -74.03653865351028}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b895827f964a5206c2d32e3',
       'name': 'Pilo Arts Day Spa and Salon',
       'location': {'address': '8412 3rd Ave',
        'lat': 40.62474788273414,
        'lng': -74.03059056940135,
        'labeledLatL

In [53]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [54]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat        lng
0  Pilo Arts Day Spa and Salon             Spa  40.624748 -74.030591
1                    Bagel Boy      Bagel Shop  40.627896 -74.029335
2          Leo's Casa Calamari     Pizza Place  40.624200 -74.030931
3                Cocoa Grinder       Juice Bar  40.623967 -74.030863
4                 Pegasus Cafe  Breakfast Spot  40.623168 -74.031186

In [55]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

85 venues were returned by Foursquare.


# Exploring Neighborhoods in Brooklyn

In [56]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [57]:
brooklyn_venues = getNearbyVenues(names=brooklyn_data['Neighborhood'],
                                   latitudes=brooklyn_data['Latitude'],
                                   longitudes=brooklyn_data['Longitude']
                                  )

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


In [58]:
print(brooklyn_venues.shape)
brooklyn_venues.head()

(2795, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Bay Ridge              40.625801              -74.030621   
1    Bay Ridge              40.625801              -74.030621   
2    Bay Ridge              40.625801              -74.030621   
3    Bay Ridge              40.625801              -74.030621   
4    Bay Ridge              40.625801              -74.030621   

                         Venue  Venue Latitude  Venue Longitude  \
0  Pilo Arts Day Spa and Salon       40.624748       -74.030591   
1                    Bagel Boy       40.627896       -74.029335   
2          Leo's Casa Calamari       40.624200       -74.030931   
3                Cocoa Grinder       40.623967       -74.030863   
4                 Pegasus Cafe       40.623168       -74.031186   

   Venue Category  
0             Spa  
1      Bagel Shop  
2     Pizza Place  
3       Juice Bar  
4  Breakfast Spot

In [59]:
brooklyn_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Bath Beach                                    49                      49   
Bay Ridge                                     85                      85   
Bedford Stuyvesant                            27                      27   
Bensonhurst                                   31                      31   
Bergen Beach                                   6                       6   
Boerum Hill                                   95                      95   
Borough Park                                  21                      21   
Brighton Beach                                45                      45   
Broadway Junction                             19                      19   
Brooklyn Heights                             100                     100   
Brownsville                                   19                      19   
Bushwick                                      72                      72   
Canarsie                                       5                       5   
Carroll Gardens                              100                     100   
City Line                                     36                      36   
Clinton Hill                                  98                      98   
Cobble Hill                                   98                      98   
Coney Island                                  17                      17   
Crown Heights                                 23                      23   
Cypress Hills                                 26                      26   
Ditmas Park                                   48                      48   
Downtown                                     100                     100   
Dumbo                                         71                      71   
Dyker Heights                                  8                       8   
East Flatbush                                 13                      13   
East New York                                 11                      11   
East Williamsburg                             69                      69   
Erasmus                                       24                      24   
Flatbush                                      23                      23   
Flatlands                                     20                      20   
Fort Greene                                   67                      67   
Fort Hamilton                                 72                      72   
Fulton Ferry                                  58                      58   
Georgetown                                    30                      30   
Gerritsen Beach                               18                      18   
Gowanus                                       62                      62   
Gravesend                                     26                      26   
Greenpoint                                   100                     100   
Highland Park                                 12                      12   
Homecrest                                     40                      40   
Kensington                                    35                      35   
Madison                                       11                      11   
Manhattan Beach                               10                      10   
Manhattan Terrace                             24                      24   
Marine Park                                   10                      10   
Midwood                                       10                      10   
Mill Basin                                    36                      36   
Mill Island                                    1                       1   
New Lots                                      22                      22   
North Side                                   100                     100   
Ocean Hill                                    31                      31   

In [60]:
print('There are {} uniques categories.'.format(len(brooklyn_venues['Venue Category'].unique())))

There are 291 uniques categories.


# Analyzing Each Neighborhood in Brooklyn

In [61]:
brooklyn_onehot = pd.get_dummies(brooklyn_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
brooklyn_onehot['Neighborhood'] = brooklyn_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [brooklyn_onehot.columns[-1]] + list(brooklyn_onehot.columns[:-1])
brooklyn_onehot = brooklyn_onehot[fixed_columns]

brooklyn_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  American Restaurant  \
0            0                  0               0                    0   
1            0                  0               0                    0   
2            0                  0               0                    0   
3            0                  0               0                    0   
4            0                  0               0                    0   

   Antique Shop  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0             0                 0                       0            0   
1             0                 0                       0            0   
2             0                 0                       0            0   
3             0                 0                       0            0   
4             0                 0                       0            0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Bagel Shop  \
0                   0            0              0          0           0   
1                   0            0              0          0           1   
2                   0            0              0          0           0   
3                   0            0              0          0           0   
4                   0            0              0          0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Beach  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0      0         0            0           0              0   
1      0         0            0           0              0   
2      0         0            0           0              0   
3      0         0            0           0              0   
4      0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bistro  Board Shop  Boat or Ferry  \
0                         0          0       0           0              0   
1                         0          0       0           0              0   
2                         0          0       0           0              0   
3                         0          0       0           0              0   
4                         0          0       0           0              0   

   Bookstore  Boutique  Boxing Gym  Breakfast Spot  Brewery  Bridge  \
0          0         0           0               0        0       0   
1          0         0           0               0        0       0   
2          0         0           0               0        0       0   
3          0         0           0               0        0       0   
4          0         0           0               1        0       0   

   Bubble Tea Shop  Buffet  Burger Joint  Burmese Restaurant  Burrito Place  \
0                0       0             0                   0              0   
1                0       0             0                   0              0   
2                0       0             0                   0              0   
3                0       0             0                   0              0   
4                0       0             0                   0              0   

   Bus Line  Bus Station  Bus Stop  Business Service  Butcher  C

In [62]:
brooklyn_onehot.shape

(2795, 291)

In [63]:
brooklyn_grouped = brooklyn_onehot.groupby('Neighborhood').mean().reset_index()
brooklyn_grouped

Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0                  Bath Beach     0.000000           0.000000            0.00   
1                   Bay Ridge     0.011765           0.000000            0.00   
2          Bedford Stuyvesant     0.000000           0.000000            0.00   
3                 Bensonhurst     0.000000           0.000000            0.00   
4                Bergen Beach     0.000000           0.000000            0.00   
5                 Boerum Hill     0.021053           0.000000            0.00   
6                Borough Park     0.000000           0.000000            0.00   
7              Brighton Beach     0.000000           0.000000            0.00   
8           Broadway Junction     0.000000           0.000000            0.00   
9            Brooklyn Heights     0.040000           0.000000            0.00   
10                Brownsville     0.000000           0.000000            0.00   
11                   Bushwick     0.000000           0.000000            0.00   
12                   Canarsie     0.000000           0.000000            0.00   
13            Carroll Gardens     0.000000           0.000000            0.00   
14                  City Line     0.000000           0.000000            0.00   
15               Clinton Hill     0.030612           0.000000            0.00   
16                Cobble Hill     0.030612           0.000000            0.00   
17               Coney Island     0.000000           0.000000            0.00   
18              Crown Heights     0.000000           0.000000            0.00   
19              Cypress Hills     0.000000           0.000000            0.00   
20                Ditmas Park     0.020833           0.000000            0.00   
21                   Downtown     0.010000           0.000000            0.00   
22                      Dumbo     0.014085           0.000000            0.00   
23              Dyker Heights     0.000000           0.000000            0.00   
24              East Flatbush     0.000000           0.000000            0.00   
25              East New York     0.000000           0.000000            0.00   
26          East Williamsburg     0.000000           0.000000            0.00   
27                    Erasmus     0.041667           0.000000            0.00   
28                   Flatbush     0.000000           0.000000            0.00   
29                  Flatlands     0.000000           0.000000            0.00   
30                Fort Greene     0.014925           0.000000            0.00   
31              Fort Hamilton     0.000000           0.000000            0.00   
32               Fulton Ferry     0.000000           0.000000            0.00   
33                 Georgetown     0.000000           0.000000            0.00   
34            Gerritsen Beach     0.000000           0.000000            0.00   
35                    Gowanus     0.016129           0.000000            0.00   
36                  Gravesend     0.000000           0.000000            0.00   
37                 Greenpoint     0.030000           0.000000            0.00   
38              Highland Park     0.000000           0.000000            0.00   
39                  Homecrest     0.000000           0.000000            0.00   
40                 Kensington     0.000000           0.000000            0.00   
41                    Madison     0.000000           0.000000            0.00   
42            Manhattan Beach     0.000000           0.000000            0.00   
43          Manhattan Terrace     0.000000           0.000000            0.00   
44                Marine Park     0.000000           0.000000            0.00   
45                    Midwood     0.000000           0.000000            0.00   
46                 Mill Basin     0.000000           0.000000            0.00   
47                Mill Island     0.000000           0.000000            0.00   
48                   New Lots     0.000000      

In [64]:
brooklyn_grouped.shape

(70, 291)

In [65]:
num_top_venues = 5

for hood in brooklyn_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = brooklyn_grouped[brooklyn_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                  venue  freq
0    Chinese Restaurant  0.10
1              Pharmacy  0.06
2           Gas Station  0.04
3  Fast Food Restaurant  0.04
4    Italian Restaurant  0.04


----Bay Ridge----
                 venue  freq
0          Pizza Place  0.06
1                  Spa  0.06
2   Italian Restaurant  0.06
3                  Bar  0.04
4  American Restaurant  0.04


----Bedford Stuyvesant----
                 venue  freq
0          Coffee Shop  0.07
1                 Café  0.07
2                  Bar  0.07
3          Pizza Place  0.07
4  Japanese Restaurant  0.04


----Bensonhurst----
                venue  freq
0  Italian Restaurant  0.10
1    Sushi Restaurant  0.06
2          Donut Shop  0.06
3  Chinese Restaurant  0.06
4         Flower Shop  0.06


----Bergen Beach----
                venue  freq
0     Harbor / Marina  0.33
1          Donut Shop  0.17
2  Athletics & Sports  0.17
3          Playground  0.17
4      Baseball Field  0.17


----Boerum Hill----
 

              venue  freq
0       Pizza Place   0.4
1    Ice Cream Shop   0.1
2       Candy Store   0.1
3            Bakery   0.1
4  Video Game Store   0.1


----Mill Basin----
                 venue  freq
0  Japanese Restaurant  0.08
1   Chinese Restaurant  0.08
2          Pizza Place  0.08
3                 Bank  0.06
4     Sushi Restaurant  0.06


----Mill Island----
                     venue  freq
0                     Pool   1.0
1              Yoga Studio   0.0
2  North Indian Restaurant   0.0
3        Other Repair Shop   0.0
4          Other Nightlife   0.0


----New Lots----
                 venue  freq
0        Grocery Store  0.09
1  Fried Chicken Joint  0.09
2   Chinese Restaurant  0.09
3          Pizza Place  0.09
4             Bus Stop  0.05


----North Side----
           venue  freq
0    Coffee Shop  0.08
1    Pizza Place  0.05
2       Wine Bar  0.03
3         Bakery  0.03
4  Jewelry Store  0.03


----Ocean Hill----
                             venue  freq
0              

In [66]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [67]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = brooklyn_grouped['Neighborhood']

for ind in np.arange(brooklyn_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(brooklyn_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach    Chinese Restaurant              Pharmacy   
1           Bay Ridge                   Spa           Pizza Place   
2  Bedford Stuyvesant                   Bar           Coffee Shop   
3         Bensonhurst    Italian Restaurant           Flower Shop   
4        Bergen Beach       Harbor / Marina        Baseball Field   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Gas Station       Bubble Tea Shop    Italian Restaurant   
1    Italian Restaurant   American Restaurant      Greek Restaurant   
2           Pizza Place                  Café              Bus Stop   
3        Ice Cream Shop      Sushi Restaurant    Chinese Restaurant   
4    Athletics & Sports            Playground            Donut Shop   

  6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0      Asian Restaurant     Fast Food Restaurant      Sushi Restaurant   
1            Bagel Shop                      Bar        Sandwich Place   
2   Fried Chicken Joint  Fruit & Vegetable Store              Boutique   
3            Donut Shop               Bagel Shop                Bakery   
4        Farmers Market     Fast Food Restaurant                 Field   

      9th Most Common Venue    10th Most Common Venue  
0     Check Cashing Service  Bike Rental / Bike Share  
1  Mediterranean Restaurant           Thai Restaurant  
2   New American Restaurant                 Gift Shop  
3               Supermarket            Cha Chaan Teng  
4       Filipino Restaurant         Fish & Chips Shop

# Cluster Brooklyn Neighborhoods with k-means

In [68]:
# set number of clusters
kclusters = 5

brooklyn_grouped_clustering = brooklyn_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(brooklyn_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [69]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

brooklyn_merged = brooklyn_data

brooklyn_merged = brooklyn_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

brooklyn_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Brooklyn    Bay Ridge  40.625801 -74.030621               1   
1  Brooklyn  Bensonhurst  40.611009 -73.995180               1   
2  Brooklyn  Sunset Park  40.645103 -74.010316               1   
3  Brooklyn   Greenpoint  40.730201 -73.954241               1   
4  Brooklyn    Gravesend  40.595260 -73.973471               1   

  1st Most Common Venue      2nd Most Common Venue 3rd Most Common Venue  \
0                   Spa                Pizza Place    Italian Restaurant   
1    Italian Restaurant                Flower Shop        Ice Cream Shop   
2           Pizza Place  Latin American Restaurant                  Bank   
3                   Bar                Pizza Place          Cocktail Bar   
4                Bakery         Chinese Restaurant           Pizza Place   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0   American Restaurant      Greek Restaurant            Bagel Shop   
1      Sushi Restaurant    Chinese Restaurant            Donut Shop   
2                Bakery    Mexican Restaurant              Pharmacy   
3           Coffee Shop           Yoga Studio           Record Shop   
4           Bus Station                Lounge              Pharmacy   

  7th Most Common Venue 8th Most Common Venue     9th Most Common Venue  \
0                   Bar        Sandwich Place  Mediterranean Restaurant   
1            Bagel Shop                Bakery               Supermarket   
2     Mobile Phone Shop                   Gym       Fried Chicken Joint   
3    Mexican Restaurant      Sushi Restaurant         French Restaurant   
4            Donut Shop           Record Shop            Cosmetics Shop   

  10th Most Common Venue  
0        Thai Restaurant  
1         Cha Chaan Teng  
2          Women's Store  
3          Deli / Bodega  
4            Music Store

In [70]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(brooklyn_merged['Latitude'], brooklyn_merged['Longitude'], brooklyn_merged['Neighborhood'], brooklyn_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examine Brooklyn Clusters

### Cluster 1

In [71]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 0, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
10        East Flatbush         Grocery Store                  Park   
27        Starrett City           Supermarket            Donut Shop   
28             Canarsie                   Gym      Asian Restaurant   
29            Flatlands              Pharmacy   Fried Chicken Joint   
32         Coney Island           Pizza Place  Caribbean Restaurant   
47  Prospect Park South  Caribbean Restaurant         Grocery Store   
56                Rugby  Caribbean Restaurant         Grocery Store   
57       Remsen Village  Caribbean Restaurant  Fast Food Restaurant   
69              Erasmus  Caribbean Restaurant    Chinese Restaurant   

   3rd Most Common Venue         4th Most Common Venue 5th Most Common Venue  \
10      Department Store             Food & Drink Shop           Supermarket   
27          Intersection                      Bus Stop         Shopping Mall   
28           IT Services            Chinese Restaurant  Caribbean Restaurant   
29  Fast Food Restaurant          Caribbean Restaurant                  Park   
32      Baseball Stadium  Theme Park Ride / Attraction               Brewery   
47           Pizza Place          Fast Food Restaurant     Mobile Phone Shop   
56                  Bank           Fried Chicken Joint                Bakery   
57   Fried Chicken Joint                   Supermarket              Pharmacy   
69         Grocery Store                   Yoga Studio                  Bank   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
10       Fast Food Restaurant  Caribbean Restaurant    Chinese Restaurant   
27                   Pharmacy  Caribbean Restaurant   American Restaurant   
28             Farmers Market  Fast Food Restaurant                 Field   
29                  Nightclub    Seafood Restaurant                Lounge   
32               Dessert Shop          Skating Rink           Music Venue   
47  Latin American Restaurant            Donut Shop        Clothing Store   
56                      Diner              Pharmacy        Sandwich Place   
57                 Donut Shop           Coffee Shop        Sandwich Place   
69                   Pharmacy            Donut Shop     Convenience Store   

   9th Most Common Venue 10th Most Common Venue  
10        Hardware Store          Moving Target  
27         Moving Target            Pizza Place  
28   Filipino Restaurant      Fish & Chips Shop  
29    Chinese Restaurant      Electronics Store  
32                 Beach    Monument / Landmark  
47   Fried Chicken Joint     Mexican Restaurant  
56  Fast Food Restaurant     Seafood Restaurant  
57                  Café            Fish Market  
69                School            Music Venue

### Cluster 2

In [72]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 1, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
0                   Bay Ridge                   Spa   
1                 Bensonhurst    Italian Restaurant   
2                 Sunset Park           Pizza Place   
3                  Greenpoint                   Bar   
4                   Gravesend                Bakery   
5              Brighton Beach            Restaurant   
6              Sheepshead Bay          Dessert Shop   
7           Manhattan Terrace           Pizza Place   
8                    Flatbush  Caribbean Restaurant   
9               Crown Heights           Pizza Place   
11                 Kensington       Thai Restaurant   
12            Windsor Terrace                 Diner   
13           Prospect Heights                   Bar   
14                Brownsville            Restaurant   
15               Williamsburg                   Bar   
16                   Bushwick                   Bar   
17         Bedford Stuyvesant                   Bar   
18           Brooklyn Heights           Yoga Studio   
19                Cobble Hill                   Bar   
20            Carroll Gardens    Italian Restaurant   
21                   Red Hook    Seafood Restaurant   
22                    Gowanus                   Bar   
23                Fort Greene    Italian Restaurant   
24                 Park Slope          Burger Joint   
25              Cypress Hills   Fried Chicken Joint   
26              East New York    Spanish Restaurant   
31            Manhattan Beach              Bus Stop   
33                 Bath Beach    Chinese Restaurant   
34               Borough Park                  Bank   
35              Dyker Heights          Dance Studio   
36            Gerritsen Beach        Ice Cream Shop   
37                Marine Park        Ice Cream Shop   
38               Clinton Hill           Pizza Place   
39                   Sea Gate                   Spa   
40                   Downtown          Burger Joint   
41                Boerum Hill          Dance Studio   
42  Prospect Lefferts Gardens                  Café   
43                 Ocean Hill         Deli / Bodega   
44                  City Line            Donut Shop   
45               Bergen Beach       Harbor / Marina   
48                 Georgetown                  Bank   
49          East Williamsburg                   Bar   
50                 North Side           Coffee Shop   
51                 South Side                   Bar   
52              Ocean Parkway     Indian Restaurant   
53              Fort Hamilton         Deli / Bodega   
54                Ditmas Park  Caribbean Restaurant   
55                    Wingate   Fried Chicken Joint   
58                   New Lots           Pizza Place   
60                 Mill Basin    Chinese Restaurant   
61               Fulton Ferry                  Park   
62               Vinegar Hill            Food Truck   
63                 Weeksville         Grocery Store   
64          Broadway Junction   Fried Chicken Joint   
65                      Dumbo           Coffee Shop   
66                  Homecrest         Grocery Store   
67              Highland Park         Grocery Store   
68                    Madison            Bagel Shop   

        2nd Most Common Venue 3rd Most Common Venue  \
0                 Pizza Place    Italian Restaurant   
1                 Flower Shop        Ice Cream Shop   
2   Latin American Restaurant                  Bank   
3                 Pizza Place          Cocktail Bar   
4          Chinese Restaurant           Pizza Place   
5                       Beach    Russian Restaurant   
6          Turkish Restaurant        Sandwich Place   
7              Ice Cream Shop            Donut Shop   
8               Deli / Bodega    Mexican Restaurant   
9                        Café                Museum   
11              Grocery Store           Pizza Place   
12              Deli / Bodega         Grocery Store   
13         Mexican Restaurant                Bakery   
1

### Cluster 3

In [73]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 2, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
30  Mill Island                  Pool         Deli / Bodega   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
30                  Farm        Farmers Market  Fast Food Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
30                 Field   Filipino Restaurant     Fish & Chips Shop   

   9th Most Common Venue 10th Most Common Venue  
30           Fish Market            Flea Market

### Cluster 4

In [74]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 3, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
46      Midwood           Pizza Place        Ice Cream Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
46      Video Game Store                Bakery           Candy Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
46     Convenience Store              Pharmacy                  Food   

   9th Most Common Venue 10th Most Common Venue  
46     Food & Drink Shop             Food Court

### Cluster 5

In [75]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 4, brooklyn_merged.columns[[1] + list(range(5, brooklyn_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
59  Paerdegat Basin         Moving Target      Asian Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
59       Harbor / Marina                  Food                   Gym   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
59                  Farm        Farmers Market  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
59                 Field    Filipino Restaurant

# Queens Data

In [76]:
queens_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
queens_data.head()

Borough     Neighborhood   Latitude  Longitude
0  Queens          Astoria  40.768509 -73.915654
1  Queens         Woodside  40.746349 -73.901842
2  Queens  Jackson Heights  40.751981 -73.882821
3  Queens         Elmhurst  40.744049 -73.881656
4  Queens     Howard Beach  40.654225 -73.838138

In [77]:
address = 'Queens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7498243, -73.7976337.


In [78]:

map_queens = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(queens_data['Latitude'], queens_data['Longitude'], queens_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_queens)  
    
map_queens

In [79]:
queens_data.loc[0, 'Neighborhood']

'Astoria'

In [80]:
neighborhood_latitude = queens_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = queens_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = queens_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Astoria are 40.76850859335492, -73.91565374304234.


In [81]:
radius=500
LIMIT=100

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

In [82]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e85f07aa2e538001b6fce39'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Astoria',
  'headerFullLocation': 'Astoria, Queens',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 106,
  'suggestedBounds': {'ne': {'lat': 40.773008597854925,
    'lng': -73.90972309237958},
   'sw': {'lat': 40.76400858885492, 'lng': -73.9215843937051}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4bdf502a89ca76b062b75d5e',
       'name': 'Favela Grill',
       'location': {'address': '33-18 28th Ave',
        'crossStreet': 'btwn 33rd & 34th St.',
        'lat': 40.76734843380796,
        'lng': -73.9178974

In [83]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [84]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name            categories        lat        lng
0        Favela Grill  Brazilian Restaurant  40.767348 -73.917897
1      Orange Blossom          Gourmet Shop  40.769856 -73.917012
2    Titan Foods Inc.          Gourmet Shop  40.769198 -73.919253
3     CrossFit Queens                   Gym  40.769404 -73.918977
4  Simply Fit Astoria                   Gym  40.769114 -73.912403

In [85]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


# Exploring Neighborhoods in Queens

In [86]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [87]:
queens_venues = getNearbyVenues(names=queens_data['Neighborhood'],
                                   latitudes=queens_data['Latitude'],
                                   longitudes=queens_data['Longitude']
                                  )

Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


In [88]:
print(queens_venues.shape)
queens_venues.head()

(2098, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0        Favela Grill       40.767348       -73.917897  Brazilian Restaurant  
1      Orange Blossom       40.769856       -73.917012          Gourmet Shop  
2    Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop  
3     CrossFit Queens       40.769404       -73.918977                   Gym  
4  Simply Fit Astoria       40.769114       -73.912403                   Gym

In [89]:
queens_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                  18                      18     18   
Astoria                                 100                     100    100   
Astoria Heights                          11                      11     11   
Auburndale                               18                      18     18   
Bay Terrace                              38                      38     38   
Bayside                                  75                      75     75   
Bayswater                                 2                       2      2   
Beechhurst                               14                      14     14   
Bellaire                                 14                      14     14   
Belle Harbor                             16                      16     16   
Bellerose                                21                      21     21   
Blissville                               18                      18     18   
Breezy Point                              4                       4      4   
Briarwood                                 8                       8      8   
Broad Channel                             5                       5      5   
Brookville                                1                       1      1   
Cambria Heights                          13                      13     13   
College Point                            37                      37     37   
Corona                                   17                      17     17   
Douglaston                               19                      19     19   
East Elmhurst                            12                      12     12   
Edgemere                                 14                      14     14   
Elmhurst                                 36                      36     36   
Far Rockaway                             32                      32     32   
Floral Park                               6                       6      6   
Flushing                                 53                      53     53   
Forest Hills                             37                      37     37   
Forest Hills Gardens                     23                      23     23   
Fresh Meadows                            14                      14     14   
Glen Oaks                                22                      22     22   
Glendale                                  5                       5      5   
Hammels                                  16                      16     16   
Hillcrest                                16                      16     16   
Hollis                                   15                      15     15   
Holliswood                                5                       5      5   
Howard Beach                             39                      39     39   
Hunters Point                            71                      71     71   
Jackson Heights                          80                      80     80   
Jamaica Center                           46                      46     46   
Jamaica Estates                           5                       5      5   
Jamaica Hills                            29                      29     29   
Kew Gardens                              43                      43     43   
Kew Gardens Hills                        20                      20     20   
Laurelton                                 6                       6      6   
Lefrak City                              23                      23     23   
Lindenwood                               14                      14     14   
Little Neck                              56                      56     56   
Long Island City                         70                      70     70   
Malba                                     3                       3      3   
Maspeth                                  32 

In [90]:
print('There are {} uniques categories.'.format(len(queens_venues['Venue Category'].unique())))

There are 272 uniques categories.


# Analayzing Each Neighborhoodhood in Queens

In [91]:
queens_onehot = pd.get_dummies(queens_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
queens_onehot['Neighborhood'] = queens_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [queens_onehot.columns[-1]] + list(queens_onehot.columns[:-1])
queens_onehot = queens_onehot[fixed_columns]

queens_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport Terminal  \
0            0                  0                  0                 0   
1            0                  0                  0                 0   
2            0                  0                  0                 0   
3            0                  0                  0                 0   
4            0                  0                  0                 0   

   American Restaurant  Antique Shop  Arepa Restaurant  \
0                    0             0                 0   
1                    0             0                 0   
2                    0             0                 0   
3                    0             0                 0   
4                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0          0           0       0     0    0               0   
1                0          0           0       0     0    0               0   
2                0          0           0       0     0    0               0   
3                0          0           0       0     0    0               0   
4                0          0           0       0     0    0               0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                 0           0      0          0                0   
1                 0           0      0          0                0   
2                 0           0      0          0                0   
3                 0           0      0          0                0   
4                 0           0      0          0                0   

   Beer Garden  Bike Trail  Bistro  Board Shop  Bookstore  Boutique  \
0            0           0       0           0          0         0   
1            0           0       0           0          0         0   
2            0           0       0           0          0         0   
3            0           0       0           0          0         0   
4            0           0       0           0          0         0   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0              0                     1               0        0            0   
1              0                     0               0        0            0   
2              0                     0               0        0            0   
3              0                     0               0        0            0   
4              0                     0               0        0            0   

   Bubble Tea Shop  Buffet  Burger Joint  Burrito Place  Bus Line  \
0                0       0             0              0         0   
1                0       0             0              0         0   
2                0       0             0              0         0   
3                0       0             0              0         0   
4                0       0             0              0         0   

   Bus Station  Bus Stop  Business Service  Butcher  Café  \
0            0         0                 0        0     0   
1            0      

In [92]:
queens_onehot.shape

(2098, 272)

In [93]:
queens_grouped = queens_onehot.groupby('Neighborhood').mean().reset_index()
queens_grouped

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0                Arverne     0.000000           0.000000           0.000000   
1                Astoria     0.000000           0.000000           0.000000   
2        Astoria Heights     0.000000           0.000000           0.000000   
3             Auburndale     0.000000           0.000000           0.000000   
4            Bay Terrace     0.000000           0.026316           0.000000   
5                Bayside     0.013333           0.000000           0.000000   
6              Bayswater     0.000000           0.000000           0.000000   
7             Beechhurst     0.071429           0.000000           0.000000   
8               Bellaire     0.000000           0.000000           0.000000   
9           Belle Harbor     0.000000           0.000000           0.000000   
10             Bellerose     0.000000           0.000000           0.000000   
11            Blissville     0.000000           0.000000           0.000000   
12          Breezy Point     0.000000           0.000000           0.000000   
13             Briarwood     0.000000           0.000000           0.000000   
14         Broad Channel     0.000000           0.000000           0.000000   
15            Brookville     0.000000           0.000000           0.000000   
16       Cambria Heights     0.000000           0.000000           0.000000   
17         College Point     0.000000           0.000000           0.000000   
18                Corona     0.000000           0.000000           0.000000   
19            Douglaston     0.000000           0.000000           0.000000   
20         East Elmhurst     0.000000           0.000000           0.000000   
21              Edgemere     0.000000           0.000000           0.000000   
22              Elmhurst     0.000000           0.000000           0.000000   
23          Far Rockaway     0.000000           0.000000           0.000000   
24           Floral Park     0.000000           0.000000           0.000000   
25              Flushing     0.018868           0.000000           0.000000   
26          Forest Hills     0.054054           0.000000           0.000000   
27  Forest Hills Gardens     0.000000           0.000000           0.000000   
28         Fresh Meadows     0.000000           0.000000           0.000000   
29             Glen Oaks     0.000000           0.000000           0.000000   
30              Glendale     0.000000           0.000000           0.000000   
31               Hammels     0.000000           0.000000           0.000000   
32             Hillcrest     0.000000           0.000000           0.000000   
33                Hollis     0.000000           0.000000           0.000000   
34            Holliswood     0.000000           0.000000           0.000000   
35          Howard Beach     0.000000           0.000000           0.000000   
36         Hunters Point     0.014085           0.000000           0.000000   
37       Jackson Heights     0.000000           0.000000           0.000000   
38        Jamaica Center     0.000000           0.000000           0.000000   
39       Jamaica Estates     0.000000           0.000000           0.000000   
40         Jamaica Hills     0.000000           0.000000           0.000000   
41           Kew Gardens     0.000000           0.000000           0.000000   
42     Kew Gardens Hills     0.000000           0.000000           0.000000   
43             Laurelton     0.000000           0.000000           0.000000   
44           Lefrak City     0.000000           0.000000           0.000000   
45            Lindenwood     0.000000           0.000000           0.000000   
46           Little Neck     0.000000           0.000000           0.000000   
47      Long Island City     0.000000           0.000000           0.000000   
48                 Malba     0.000000           0.000000           0.000000   
49               Maspeth     0.000000           0.000000      

In [94]:
queens_grouped.shape

(81, 272)

In [95]:
num_top_venues = 5

for hood in queens_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = queens_grouped[queens_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
            venue  freq
0       Surf Spot  0.22
1  Sandwich Place  0.11
2   Metro Station  0.11
3           Beach  0.06
4     Coffee Shop  0.06


----Astoria----
                       venue  freq
0                        Bar  0.07
1                 Hookah Bar  0.06
2  Middle Eastern Restaurant  0.05
3           Greek Restaurant  0.05
4         Seafood Restaurant  0.04


----Astoria Heights----
                venue  freq
0       Shopping Mall  0.09
1         Bus Station  0.09
2        Burger Joint  0.09
3  Italian Restaurant  0.09
4       Bowling Alley  0.09


----Auburndale----
                venue  freq
0  Italian Restaurant  0.11
1   Mobile Phone Shop  0.06
2          Hookah Bar  0.06
3      Gymnastics Gym  0.06
4    Sushi Restaurant  0.06


----Bay Terrace----
               venue  freq
0     Clothing Store  0.11
1         Kids Store  0.05
2  Mobile Phone Shop  0.05
3     Lingerie Store  0.05
4     Cosmetics Shop  0.05


----Bayside----
                 venue  fre

              venue  freq
0  Department Store  0.09
1    Cosmetics Shop  0.09
2            Bakery  0.09
3     Women's Store  0.04
4      Liquor Store  0.04


----Lindenwood----
           venue  freq
0   Dance Studio  0.07
1     Donut Shop  0.07
2  Grocery Store  0.07
3           Bank  0.07
4         Bakery  0.07


----Little Neck----
                 venue  freq
0   Chinese Restaurant  0.07
1   Italian Restaurant  0.05
2    Korean Restaurant  0.05
3        Deli / Bodega  0.05
4  Japanese Restaurant  0.04


----Long Island City----
                venue  freq
0               Hotel  0.11
1         Coffee Shop  0.11
2         Pizza Place  0.06
3                 Bar  0.06
4  Mexican Restaurant  0.04


----Malba----
                       venue  freq
0  Latin American Restaurant  0.33
1                  Rest Area  0.33
2               Tennis Court  0.33
3                Yoga Studio  0.00
4                  Nightclub  0.00


----Maspeth----
                venue  freq
0         Pizza Place 

In [96]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [97]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = queens_grouped['Neighborhood']

for ind in np.arange(queens_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(queens_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Arverne             Surf Spot         Metro Station   
1          Astoria                   Bar            Hookah Bar   
2  Astoria Heights                Hostel         Bowling Alley   
3       Auburndale    Italian Restaurant    Miscellaneous Shop   
4      Bay Terrace        Clothing Store         Women's Store   

  3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  \
0        Sandwich Place                Coffee Shop            Board Shop   
1      Greek Restaurant  Middle Eastern Restaurant    Seafood Restaurant   
2                Bakery                Supermarket         Shopping Mall   
3        Gymnastics Gym               Noodle House           Supermarket   
4            Shoe Store                 Kids Store   American Restaurant   

  6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
0              Bus Stop           Bed & Breakfast                 Beach   
1                  Café  Mediterranean Restaurant     Indian Restaurant   
2    Italian Restaurant               Bus Station          Burger Joint   
3     Korean Restaurant    Furniture / Home Store    Athletics & Sports   
4        Lingerie Store         Mobile Phone Shop        Cosmetics Shop   

  9th Most Common Venue 10th Most Common Venue  
0       Thai Restaurant             Donut Shop  
1       Bubble Tea Shop                    Pub  
2           Pizza Place             Playground  
3        Discount Store       Toy / Game Store  
4            Donut Shop               Pharmacy

# Cluster Queens' Neighborhoods with K-Means

In [98]:
# set number of clusters
kclusters = 5

queens_grouped_clustering = queens_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(queens_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([4, 4, 4, 4, 4, 4, 0, 4, 4, 1], dtype=int32)

In [99]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

queens_merged = queens_data

queens_merged = queens_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

queens_merged.head() # check the last columns!

Borough     Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Queens          Astoria  40.768509 -73.915654               4   
1  Queens         Woodside  40.746349 -73.901842               4   
2  Queens  Jackson Heights  40.751981 -73.882821               4   
3  Queens         Elmhurst  40.744049 -73.881656               4   
4  Queens     Howard Beach  40.654225 -73.838138               4   

       1st Most Common Venue 2nd Most Common Venue      3rd Most Common Venue  \
0                        Bar            Hookah Bar           Greek Restaurant   
1              Grocery Store       Thai Restaurant  Latin American Restaurant   
2  Latin American Restaurant   Peruvian Restaurant  South American Restaurant   
3            Thai Restaurant    Mexican Restaurant  South American Restaurant   
4         Italian Restaurant            Bagel Shop       Fast Food Restaurant   

       4th Most Common Venue  5th Most Common Venue 6th Most Common Venue  \
0  Middle Eastern Restaurant     Seafood Restaurant                  Café   
1                     Bakery    Filipino Restaurant           Pizza Place   
2                     Bakery     Mexican Restaurant     Mobile Phone Shop   
3         Chinese Restaurant  Vietnamese Restaurant       Bubble Tea Shop   
4                   Pharmacy          Deli / Bodega        Sandwich Place   

      7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0  Mediterranean Restaurant     Indian Restaurant       Bubble Tea Shop   
1       American Restaurant                   Bar            Donut Shop   
2             Grocery Store       Thai Restaurant           Supermarket   
3               Snack Place                   Bar      Sushi Restaurant   
4          Sushi Restaurant      Tapas Restaurant   Japanese Restaurant   

  10th Most Common Venue  
0                    Pub  
1                    Pub  
2               Pharmacy  
3       Malay Restaurant  
4                   Bank

In [100]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(queens_merged['Latitude'], queens_merged['Longitude'], queens_merged['Neighborhood'], queens_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examine Queens' Clusters

### Cluster 1

In [101]:
queens_merged.loc[queens_merged['Cluster Labels'] == 0, queens_merged.columns[[1] + list(range(5, queens_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
63   Somerville                  Park        Farmers Market   
79    Bayswater                  Park            Playground   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
63   Egyptian Restaurant     Electronics Store   Empanada Restaurant   
79         Women's Store                  Farm   Egyptian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
63           Event Space    Falafel Restaurant                  Farm   
79     Electronics Store   Empanada Restaurant           Event Space   

   9th Most Common Venue       10th Most Common Venue  
63         Women's Store  Eastern European Restaurant  
79    Falafel Restaurant               Farmers Market

### Cluster 2

In [102]:
queens_merged.loc[queens_merged['Cluster Labels'] == 1, queens_merged.columns[[1] + list(range(5, queens_merged.shape[1]))]]

Neighborhood      1st Most Common Venue      2nd Most Common Venue  \
17         Woodhaven              Deli / Bodega                       Bank   
19  South Ozone Park                       Park              Deli / Bodega   
21        Whitestone              Historic Site              Deli / Bodega   
30         Briarwood              Deli / Bodega                Bus Station   
42     Broad Channel        Sporting Goods Shop              Deli / Bodega   
43      Breezy Point        Monument / Landmark                      Beach   
47          Edgemere              Metro Station                Pizza Place   
49    Rockaway Beach                      Beach  Latin American Restaurant   
61      Belle Harbor                      Beach                        Spa   
62     Rockaway Park                      Beach                Pizza Place   
66      North Corona              Deli / Bodega       Gym / Fitness Center   
69            Utopia              Deli / Bodega                        Spa   
75           Roxbury             Baseball Field              Deli / Bodega   
77             Malba  Latin American Restaurant                  Rest Area   
78           Hammels                      Beach                    Dog Run   

   3rd Most Common Venue     4th Most Common Venue 5th Most Common Venue  \
17              Pharmacy               Supermarket            Nail Salon   
19  Fast Food Restaurant                     Hotel        Sandwich Place   
21       Bubble Tea Shop               Candy Store          Dance Studio   
30                 Plaza        Mexican Restaurant  Fast Food Restaurant   
42              Dive Bar               Pizza Place       Other Nightlife   
43                 Trail                  Bus Stop           Flower Shop   
47                 Hotel            Scenic Lookout         Deli / Bodega   
49    Seafood Restaurant          Arepa Restaurant            Food Truck   
61         Deli / Bodega                       Pub    Italian Restaurant   
62                  Bank  Mediterranean Restaurant            Donut Shop   
66                Bakery        Mexican Restaurant           Pizza Place   
69   Indie Movie Theater          Basketball Court            Donut Shop   
75                 Beach                 Irish Pub                 Trail   
77          Tennis Court             Women's Store                  Farm   
78         Deli / Bodega       Fried Chicken Joint                  Café   

        6th Most Common Venue      7th Most Common Venue  \
17             Sandwich Place                  Gift Shop   
19                 Donut Shop                        Bar   
21                       Food                Flower Shop   
30                Coffee Shop        Arts & Crafts Store   
42               Dance Studio        Egyptian Restaurant   
43                Fish Market          Fish & Chips Shop   
47         Seafood Restaurant                 Skate Park   
49                  BBQ Joint                Pizza Place   
61                   Boutique                     Bakery   
62          French Restaurant                 Steakhouse   
66  South American Restaurant  Latin American Restaurant   
69                     Bakery                       Park   
75       Fast Food Restaurant              Women's Store   
77        Egyptian Restaurant          Electronics Store   
78       Gym / Fitness Center                      Diner   

   8th Most Common Venue      9th Most Common Venue 10th Most Common Venue  
17            Donut Shop                 Bagel Shop        Thai Restaurant  
19    Falafel Restaurant          Electronics Store    Empanada Restaurant  
21           Fish Market          Fish & Chips Shop      Electronics Store  
30         Women's Store                Event Space     Falafel Restaurant  
42                  Food                Flower Shop            Fish Market  
43   Filipino Restaurant       Fast Food Restaurant    Egyptian Restaurant  
47           Bus Station                  

### Cluster 3

In [103]:
queens_merged.loc[queens_merged['Cluster Labels'] == 2, queens_merged.columns[[1] + list(range(5, queens_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
50     Neponsit                 Beach         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
50        Farmers Market     Electronics Store   Empanada Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
50           Event Space    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
50  Fast Food Restaurant             Food Truck

### Cluster 4

In [104]:
queens_merged.loc[queens_merged['Cluster Labels'] == 3, queens_merged.columns[[1] + list(range(5, queens_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
64   Brookville         Deli / Bodega         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
64  Fast Food Restaurant     Electronics Store   Empanada Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
64           Event Space    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
64        Farmers Market    Filipino Restaurant

### Cluster 5

In [105]:
queens_merged.loc[queens_merged['Cluster Labels'] == 4, queens_merged.columns[[1] + list(range(5, queens_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
0                Astoria                        Bar   
1               Woodside              Grocery Store   
2        Jackson Heights  Latin American Restaurant   
3               Elmhurst            Thai Restaurant   
4           Howard Beach         Italian Restaurant   
5                 Corona         Mexican Restaurant   
6           Forest Hills       Gym / Fitness Center   
7            Kew Gardens         Chinese Restaurant   
8          Richmond Hill                     Lounge   
9               Flushing          Hotpot Restaurant   
10      Long Island City                      Hotel   
11             Sunnyside                Pizza Place   
12         East Elmhurst                 Donut Shop   
13               Maspeth                Pizza Place   
14             Ridgewood                       Bank   
15              Glendale                    Brewery   
16             Rego Park                     Bakery   
18            Ozone Park                Pizza Place   
20         College Point              Deli / Bodega   
22               Bayside                        Bar   
23            Auburndale         Italian Restaurant   
24           Little Neck         Chinese Restaurant   
25            Douglaston                       Bank   
26             Glen Oaks                   Pharmacy   
27             Bellerose                Pizza Place   
28     Kew Gardens Hills                       Bank   
29         Fresh Meadows                Bus Station   
31        Jamaica Center          Mobile Phone Shop   
32       Oakland Gardens         Chinese Restaurant   
33        Queens Village                       Bank   
34                Hollis        Fried Chicken Joint   
35         South Jamaica                Bus Station   
36            St. Albans       Caribbean Restaurant   
37              Rochdale                     Market   
38   Springfield Gardens                Bus Station   
39       Cambria Heights       Caribbean Restaurant   
40              Rosedale                Bus Station   
41          Far Rockaway              Deli / Bodega   
44              Steinway        Rental Car Location   
45            Beechhurst         Chinese Restaurant   
46           Bay Terrace             Clothing Store   
48               Arverne                  Surf Spot   
51           Murray Hill          Korean Restaurant   
52           Floral Park              Grocery Store   
53            Holliswood          Mobile Phone Shop   
54       Jamaica Estates                Bus Station   
55       Queensboro Hill         Chinese Restaurant   
56             Hillcrest                 Donut Shop   
57            Ravenswood         Chinese Restaurant   
58            Lindenwood               Dance Studio   
59             Laurelton       Caribbean Restaurant   
60           Lefrak City             Cosmetics Shop   
65              Bellaire              Deli / Bodega   
67  Forest Hills Gardens             Sandwich Place   
68         Jamaica Hills                   Pharmacy   
70               Pomonok             Scenic Lookout   
71       Astoria Heights                     Hostel   
72         Hunters Point                       Café   
73     Sunnyside Gardens                        Bar   
74            Blissville                      Hotel   
76        Middle Village             Cosmetics Shop   
80          Queensbridge                      Hotel   

              2nd Most Common Venue      3rd Most Common Venue  \
0                        Hookah Bar           Greek Restaurant   
1                   Thai Restaurant  Latin American Restaurant   
2               Peruvian Restaurant  South American Restaurant   
3                Mexican Restaurant  South American Restaurant   
4                        Bagel Shop       Fast Food Restaurant   
5                 Convenience Store                       Park   
6                               Gym                Yoga Studio   
7                 